# SEC Edgar Data Analysis

## Introduction

In this notebook, we will analyze the SEC Edgar data based on the information retrieved via the SEC's public [API](https://www.sec.gov/edgar/sec-api-documentation). 

The SEC Edgar data is a dataset of financial reports of companies that are filed with the SEC. 

The main API's are as follows:

- data.sec.gov/submissions/
- data.sec.gov/api/xbrl/companyconcept/
- data.sec.gov/api/xbrl/companyfacts/

From these API's, we can retrieve the following information:

- `cik`: The Central Index Key for the filing entity.
- `name`: The name of the entity.
- `ticker`: The ticker symbol of the entity.
- `sic`: The Standard Industrial Classification code for the filing.
- `adsh`: The Accession Number for the submission.
- `countryba`: The ISO country code for the filing's business address.
- `stprba`: The region for the filing's business address.
- `cityba`: The city for the filing's business address.
- `zipba`: The zip code for the filing's business address.
- `bas1`: The street address for the filing's business address.
- `form`: The submission type of the filing.
- `period`: The period end date.
- `fy`: The fiscal year end date.
- `fp`: The fiscal period focus (Q1, Q2, Q3, FY).
- `filed`: The date the report was filed.
- `accepted`: The date the report was accepted.
- `prevrpt`: The Accession Number for the previous report.
- `detail`: The file name of the primary financial statements and notes.
- `instance`: The file name of the XBRL instance document.
- `nciks`: The number of additional Central Index Keys for the filing.
- `aciks`: The number of additional Central Index Keys for the filing that are not included in the submission.
- `year`: The year of the filing.
- `quarter`: The quarter of the filing.
- `month`: The month of the filing.
- `day`: The day of the filing.
- `hour`: The hour of the filing.

We will analyze the dataset to understand the financial reports of companies that are filed with the SEC.

## Libraries

We will use the following libraries in this notebook:

- `pandas` for data manipulation.
- `requests` for making HTTP requests.
- `numpy` for numerical operations.
- `calendar` for calendar operations.
- `logging` for logging operations.
- `os` for file operations.

## Custom Functions

We will define the following custom functions in this notebook:

- `edgar_functions.py`: This file contains custom functions for analyzing the SEC Edgar data.


## Initialize the Environment

Let's initialize the environment by importing the required libraries and custom functions.

### Import Libraries

`Panadas` is a fast, powerful, flexible and easy to use open source data analysis and data manipulation library built on top of the Python programming language.

`Requests` is a simple HTTP library for Python that will communicate with the SEC Edgar API and retrieve the data.

`json` is a lightweight data interchange format inspired by JavaScript object literal syntax. This will be used to parse the JSON data retrieved from the SEC Edgar API.

`os` is a module in Python that provides functions for interacting with the operating system. This will be used to perform file operations such as reading and writing files.

`csv` is a module in Python that provides functions for reading and writing CSV files.

`zipfile` is a module in Python that provides functions for reading and writing ZIP files. This will be used to extract the ZIP files downloaded from the SEC Edgar API.

`logging` is a module in Python that provides a flexible framework for emitting log messages from Python programs.

`tqdm` is a module in Python that provides a fast, extensible progress bar for loops and other functions. When downloading very large files, it is helpful to have a progress bar to show the progress of the download.

`re` is a module in Python that provides support for regular expressions. This will be used to validate the input data such as the email address for the header.

In [21]:
%pip install tqdm pandas requests

ERROR: unknown command "update"
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


## Setting the headers for the API request

The SEC Edgar API requires a header to be set for the API request. The header should contain the following information:

- `User-Agent`: Sample Company Name AdminContact@<sample company domain>.com
- `Accept-Encoding`: gzip, deflate
- `Host`: www.sec.gov

## 

In [1]:
# Run this cell to configure the user agent email

import re

# Check if user_agent_email is defined and not an empty string
if 'user_agent_email' not in globals() or not user_agent_email:
    while True:
        user_agent_email = input("Please enter your user agent email: ")
        # Check if the input is in a valid email format
        if re.match(r"[^@]+@[^@]+\.[^@]+", user_agent_email):
            break
        else:
            print("Invalid email format. Please try again.")

print(f"User agent email: {user_agent_email}")

User agent email: amr@bashconsultants.com


In [2]:
# Initialize the environment

import pandas as pd
import requests
import json
import os
import csv
import zipfile
import logging

# define the headers for the requests to the SEC website. This is required to access the data, otherwise the request will be blocked
# Current max request rate: 10 requests/second.

headers = {"User-Agent": user_agent_email,
           "Accept-Encodings": "gzip, deflate"}

# Set up logging
logging.basicConfig(filename='error_log.txt', level=logging.ERROR)

# Define the function to download the index files from the SEC website based on the ticker

def cik_ticker(ticker, headers=headers):
    ticker = ticker.upper().replace(".", "-")
    ticker_json = requests.get(
        "https://www.sec.gov/files/company_tickers.json", headers=headers
    ).json()

    for company in ticker_json.values():
        if company["ticker"] == ticker:
            cik = str(company["cik_str"]).zfill(10)
            name = str(company["title"])
            return {"cik": cik, "name": name}

    raise ValueError(f"Ticker {ticker} not found in SEC database")

/Users/bamr87/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


## CIK Lookup

The Central Index Key (CIK) is a unique identifier assigned by the SEC to companies and individuals who file reports with the SEC. The CIK is used to identify the filer in the SEC's EDGAR database. The CIK is a 10-digit number that is assigned to each filer when they first file a report with the SEC.

define the ticker symbol for the company whose CIK we want to look up. We will use the `get_cik` function to look up the CIK for the company.

In [4]:
# Prompt the user for a ticker and run the function
ticker = input("Please enter a ticker: ")
cik_id = cik_ticker(ticker)
print(cik_id)

{'cik': '0000102729', 'name': 'VALMONT INDUSTRIES INC'}


## Company submission data

The SEC Edgar API provides information about the submissions made by a company. The `get_company_submission_data` function retrieves the submission data for a company based on the CIK and the filing type.

This function takes the following parameters:


In [5]:
# get the json data for the company with the CIK based on the ticker

def get_submission_data(ticker, headers=headers, only_filings_df=False):
    """
    Get the data in json form for a given ticker. For example: 'cik', 'entityType', 'sic', 'sicDescription', 'insiderTransactionForOwnerExists', 'insiderTransactionForIssuerExists', 'name', 'tickers', 'exchanges', 'ein', 'description', 'website', 'investorWebsite', 'category', 'fiscalYearEnd', 'stateOfIncorporation', 'stateOfIncorporationDescription', 'addresses', 'phone', 'flags', 'formerNames', 'filings'

    Args:
        ticker (str): The ticker symbol of the company.
        headers (dict): The headers for the request.
        only_filings_df (bool): If True, returns a DataFrame with the filings.

    Returns:
        json: The submissions for the company.
        DataFrame: The recent filings for the company.

    Raises:
        ValueError: If ticker is not a string.
    """

    cik = cik_ticker(ticker).get("cik")
    url = f"https://data.sec.gov/submissions/CIK{cik}.json"
    company_json = requests.get(url, headers=headers).json()
    if only_filings_df:
        return pd.DataFrame(company_json["filings"]["recent"])
    else:
        return company_json

## Downloading the company submission data



In [6]:
# Prompt the user for a ticker and run the function

submission_data = get_submission_data(ticker, only_filings_df=False)
print(submission_data)


{'cik': '102729', 'entityType': 'operating', 'sic': '3440', 'sicDescription': 'Fabricated Structural Metal Products', 'insiderTransactionForOwnerExists': 0, 'insiderTransactionForIssuerExists': 1, 'name': 'VALMONT INDUSTRIES INC', 'tickers': ['VMI'], 'exchanges': ['NYSE'], 'ein': '470351813', 'description': '', 'website': '', 'investorWebsite': '', 'category': 'Large accelerated filer', 'fiscalYearEnd': '1230', 'stateOfIncorporation': 'DE', 'stateOfIncorporationDescription': 'DE', 'addresses': {'mailing': {'street1': '15000 VALMONT PLAZA', 'street2': None, 'city': 'OMAHA', 'stateOrCountry': 'NE', 'zipCode': '68154', 'stateOrCountryDescription': 'NE'}, 'business': {'street1': '15000 VALMONT PLAZA', 'street2': None, 'city': 'OMAHA', 'stateOrCountry': 'NE', 'zipCode': '68154', 'stateOrCountryDescription': 'NE'}}, 'phone': '402-963-1000', 'flags': '', 'formerNames': [], 'filings': {'recent': {'accessionNumber': ['0001104659-24-038524', '0001104659-24-038523', '0001104659-24-038520', '00009

In [19]:
def export_to_json(data, cik_id, filename):
    cik = cik_id.get("cik")
    if isinstance(data, pd.DataFrame):
        data = pd.DataFrame.to_json(data)  # convert DataFrame to JSON
    with open(f'company-{filename}-{cik}.json', 'w') as json_file:
        json.dump(data, json_file, indent=3)

In [20]:
data_dict = submission_data  # replace with your actual data
filename = "submissions"
export_to_json(data_dict, cik_id, filename)

In [9]:
def get_filtered_filings(
    ticker, ten_k=True, just_accession_numbers=False, headers=headers
):
    company_filings_df = get_submission_data(
        ticker, only_filings_df=True, headers=headers
    )
    if ten_k:
        df = company_filings_df[company_filings_df["form"] == "10-K"]
    else:
        df = company_filings_df[company_filings_df["form"] == "10-Q"]
    if just_accession_numbers:
        df = df.set_index("reportDate")
        accession_df = df["accessionNumber"]
        return accession_df
    else:
        return df

In [10]:
filings = get_filtered_filings(ticker, ten_k=True, just_accession_numbers=True, headers=headers)

filings

reportDate
2023-12-30    0000102729-24-000013
2022-12-31    0000102729-23-000019
2021-12-25    0000102729-22-000008
2020-12-26    0000102729-21-000012
2019-12-28    0000102729-20-000004
2018-12-29    0000102729-19-000003
2017-12-30    0000102729-18-000008
2016-12-31    0001628280-17-002033
2015-12-26    0000102729-16-000009
2014-12-27    0001047469-15-001179
2013-12-28    0001047469-14-001292
2012-12-29    0001047469-13-001680
2011-12-31    0001047469-12-001703
2010-12-25    0001047469-11-001183
2009-12-26    0001047469-10-001156
Name: accessionNumber, dtype: object

In [11]:
# get the data for the company based on the CIK

def get_facts(ticker, headers=headers):
    cik = cik_ticker(ticker)
    url = f"https://data.sec.gov/api/xbrl/companyfacts/CIK{cik}.json"
    company_facts = requests.get(url, headers=headers).json()
    return company_facts

In [12]:
# Get the facts for the company
facts = get_facts(ticker)
facts

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [34]:
# get the account facts for the company for us-gaap

facts["facts"]["us-gaap"]

{'AccountsPayableCurrentAndNoncurrent': {'label': 'Accounts Payable',
  'description': "Carrying value as of the balance sheet date of liabilities incurred (and for which invoices have typically been received) and payable to vendors for goods and services received that are used in an entity's business.",
  'units': {'USD': [{'end': '2013-12-31',
     'val': 8313000,
     'accn': '0001562762-14-000228',
     'fy': 2014,
     'fp': 'Q2',
     'form': '10-Q',
     'filed': '2014-08-13'},
    {'end': '2013-12-31',
     'val': 8313000,
     'accn': '0001562762-14-000325',
     'fy': 2014,
     'fp': 'Q3',
     'form': '10-Q',
     'filed': '2014-11-14'},
    {'end': '2013-12-31',
     'val': 8313000,
     'accn': '0001562762-15-000061',
     'fy': 2014,
     'fp': 'FY',
     'form': '10-K',
     'filed': '2015-03-06',
     'frame': 'CY2013Q4I'},
    {'end': '2014-06-30',
     'val': 11267000,
     'accn': '0001562762-14-000228',
     'fy': 2014,
     'fp': 'Q2',
     'form': '10-Q',
     'f

In [35]:
us_gaap_levels = facts["facts"]["us-gaap"].keys()
us_gaap_levels


dict_keys(['AccountsPayableCurrentAndNoncurrent', 'AccountsPayableOtherCurrentAndNoncurrent', 'AccountsReceivableNet', 'AccrualForTaxesOtherThanIncomeTaxesCurrentAndNoncurrent', 'AccruedIncomeTaxes', 'AccruedLiabilitiesAndOtherLiabilities', 'AccumulatedDepreciationDepletionAndAmortizationPropertyPlantAndEquipment', 'AcquisitionCosts', 'AdditionalPaidInCapitalCommonStock', 'AdjustmentsToAdditionalPaidInCapitalOther', 'AdjustmentsToAdditionalPaidInCapitalSharebasedCompensationRequisiteServicePeriodRecognitionValue', 'AdjustmentsToAdditionalPaidInCapitalTaxEffectFromShareBasedCompensation', 'AllocatedShareBasedCompensationExpense', 'AllowanceForDoubtfulAccountsReceivable', 'AmortizationOfIntangibleAssets', 'AntidilutiveSecuritiesExcludedFromComputationOfEarningsPerShareAmount', 'AssetImpairmentCharges', 'Assets', 'AssetsHeldForSaleNotPartOfDisposalGroupCurrent', 'BilledContractReceivables', 'BillingsInExcessOfCost', 'BusinessAcquisitionCostOfAcquiredEntityTransactionCosts', 'BusinessAcqui

In [36]:
# export the account facts to a csv file

import csv

with open('acct_facts.csv', 'w', newline='') as f:
    writer = csv.writer(f)
    # Write headers
    writer.writerow(["us_gaap_list", "acct_label", "acct_description"])
    
    for us_gaap_list in facts["facts"]["us-gaap"]:
        acct_label = facts["facts"]["us-gaap"][us_gaap_list]["label"]
        acct_description = facts["facts"]["us-gaap"][us_gaap_list]["description"]
        print(f"{us_gaap_list}, {acct_label}, {acct_description}")
        writer.writerow([us_gaap_list, acct_label, acct_description])

AccountsPayableCurrentAndNoncurrent, Accounts Payable, Carrying value as of the balance sheet date of liabilities incurred (and for which invoices have typically been received) and payable to vendors for goods and services received that are used in an entity's business.
AccountsPayableOtherCurrentAndNoncurrent, Accounts Payable, Other, Amount of obligations incurred and payable classified as other.
AccountsReceivableNet, Accounts Receivable, after Allowance for Credit Loss, Amount, after allowance for credit loss, of right to consideration from customer for product sold and service rendered in normal course of business.
AccrualForTaxesOtherThanIncomeTaxesCurrentAndNoncurrent, Accrual for Taxes Other than Income Taxes, Carrying value as of the balance sheet date of obligations incurred and payable for real and property taxes.
AccruedIncomeTaxes, Accrued Income Taxes, Carrying amount as of the balance sheet date of the unpaid sum of the known and estimated amounts payable to satisfy all 

## Processing bulk data

In [ ]:
[sec-api-docs](https://www.sec.gov/edgar/sec-api-documentation)

https://www.sec.gov/Archives/edgar/daily-index/xbrl/companyfacts.zip

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.6/57.6 kB 1.0 MB/s eta 0:00:00ta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.3/78.3 kB 4.7 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [10]:
print(headers)

{'User-Agent': 'amr@bashconsultants.com'}


In [18]:
import requests
import requests
from tqdm import tqdm

def download_file(filename, url):
    response = requests.get(url, headers=headers, stream=True)
    total_size = int(response.headers.get('content-length', 0))
    
    with open(filename, "wb") as file, tqdm(
        desc=filename,
        total=total_size,
        unit='iB',
        unit_scale=True,
        unit_divisor=1024,
    ) as progress_bar:
        for data in response.iter_content(chunk_size=1024):
            file.write(data)
            progress_bar.update(len(data))


In [19]:
bulk_data_company_facts = download_file("companyfacts.zip", "https://www.sec.gov/Archives/edgar/daily-index/xbrl/companyfacts.zip") 


download_file("companyfacts.zip", "https://www.sec.gov/Archives/edgar/daily-index/xbrl/companyfacts.zip")


companyfacts.zip: 100%|██████████| 1.12G/1.12G [01:25<00:00, 14.2MiB/s]


In [20]:
import csv
import zipfile
import json


def facts_DF():
    with zipfile.ZipFile('companyfacts.zip', 'r') as z:
        for filename in z.namelist():
            try:
                with z.open(filename) as f:
                    facts = json.load(f)
                    if 'us-gaap' in facts["facts"]:
                        us_gaap_data = facts["facts"]["us-gaap"]
                        for fact, details in us_gaap_data.items():
                            acct_label = details["label"]
                            acct_description = details["description"]
                            yield fact, acct_label, acct_description
            except Exception as e:
                print(f"Error processing file {filename}: {e}")
                logging.error(f"Error processing file {filename}: {e}")

seen = set()

with open('acct_facts.csv', 'w', newline='') as f:
    writer = csv.writer(f)
    # Write headers
    writer.writerow(["us_gaap_list", "acct_label", "acct_description"])
    
    json_output = []
    
    for us_gaap_list, acct_label, acct_description in facts_DF():
        # Create a tuple of the row
        row = (us_gaap_list, acct_label, acct_description)
        # If we've already seen this row, skip it
        if row in seen:
            continue
        # Add the row to the set of seen rows
        seen.add(row)
        print(f"{us_gaap_list}, {acct_label}, {acct_description}")
        writer.writerow([us_gaap_list, acct_label, acct_description])
        json_output.append({
            "us_gaap_list": us_gaap_list,
            "acct_label": acct_label,
            "acct_description": acct_description
        })
    
    # Write to JSON file
    with open('acct_facts.json', 'w') as json_file:
        json.dump(json_output, json_file, indent=3)

AccountsPayableCurrent, Accounts Payable, Current, Carrying value as of the balance sheet date of liabilities incurred (and for which invoices have typically been received) and payable to vendors for goods and services received that are used in an entity's business. Used to reflect the current portion of the liabilities (due within one year or within the normal operating cycle if longer).
AccountsReceivableNetCurrent, Accounts Receivable, after Allowance for Credit Loss, Current, Amount, after allowance for credit loss, of right to consideration from customer for product sold and service rendered in normal course of business, classified as current.
AccruedLiabilitiesCurrent, Accrued Liabilities, Current, Carrying value as of the balance sheet date of obligations incurred and payable, pertaining to costs that are statutory in nature, are incurred on contractual obligations, or accumulate over time and for which invoices have not yet been received or will not be rendered. Examples includ

In [ ]:
data_dict = facts  # replace with your actual data
filename = "facts"
export_to_json(data_dict, cik_id, filename)

In [ ]:
def facts_DF(ticker, headers=headers):
    facts = get_facts(ticker, headers)
    us_gaap_data = facts["facts"]["us-gaap"]
    df_data = []
    for fact, details in us_gaap_data.items():
        for unit in details["units"]:
            for item in details["units"][unit]:
                row = item.copy()
                row["fact"] = fact
                df_data.append(row)

    df = pd.DataFrame(df_data)
    df["end"] = pd.to_datetime(df["end"])
    df["start"] = pd.to_datetime(df["start"])
    df = df.drop_duplicates(subset=["fact", "end", "val"])
    df.set_index("end", inplace=True)
    labels_dict = {fact: details["label"] for fact, details in us_gaap_data.items()}
    return df, labels_dict